# Testing inference on Network Diffusion 

Here, I will examine the utility of sampling and variational inference for inferring values from a simple network diffusion model on Erdos-Renyi random graphs. The primary aim of this document is to assess how well inference can scale as the network grows in size and as topology -- in this case, connection probability -- change. 

### Environment
First, check environment to ensure all packages needed are present and document their versions. 

In [5]:
using Pkg

In [7]:
Pkg.status();

Status `~/Projects/NetworkTopology/Project.toml`
  [76274a88] Bijectors v0.8.14
  [a93c6f00] DataFrames v0.22.5
  [0c46a032] DifferentialEquations v6.16.0
  [31c24e10] Distributions v0.24.13
  [7073ff75] IJulia v1.23.1
  [093fc24a] LightGraphs v1.3.5
  [c7f686f2] MCMCChains v4.7.0
  [91a5bcdd] Plots v1.10.4
  [37e2e3b7] ReverseDiff v1.5.0
  [f3b207a7] StatsPlots v0.14.19
  [fce5fe82] Turing v0.15.10
  [e88e6eb3] Zygote v0.6.3


In [9]:
using Random
Random.seed!(1)

MersenneTwister(UInt32[0x00000001], Random.DSFMT.DSFMT_state(Int32[1749029653, 1072851681, 1610647787, 1072862326, 1841712345, 1073426746, -198061126, 1073322060, -156153802, 1073567984  …  1977574422, 1073209915, 278919868, 1072835605, 1290372147, 18858467, 1815133874, -1716870370, 382, 0]), [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0  …  0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], UInt128[0x00000000000000000000000000000000, 0x00000000000000000000000000000000, 0x00000000000000000000000000000000, 0x00000000000000000000000000000000, 0x00000000000000000000000000000000, 0x00000000000000000000000000000000, 0x00000000000000000000000000000000, 0x00000000000000000000000000000000, 0x00000000000000000000000000000000, 0x00000000000000000000000000000000  …  0x00000000000000000000000000000000, 0x00000000000000000000000000000000, 0x00000000000000000000000000000000, 0x00000000000000000000000000000000, 0x00000000000000000000000000000000, 0x00000000000000000000000000000000, 0x000000000000

### Model Setup 

The first step in defining our model will be to initialise a graph on which to run the model. We do this using `LightGraphs` to generate a Erdos-Renyi random graph of size `N`. 

In [32]:
using LightGraphs

function make_graph(N::Int64, P::Float64)
    G = erdos_renyi(N, P)
    L = laplacian_matrix(G)
    A = adjacency_matrix(G)
    return L, A
end

N = 5
P = 0.5

L, A = make_graph(N, P);

The second step of the modelling process will be to define the ODE model. For network diffusion, this is given by: 

$$ \frac{d\mathbf{u}}{dt} = -\rho \mathbf{L} \mathbf{u} $$ 

We can set this up as a julia function as follows:

In [33]:
NetworkDiffusion(u, p, t) = -p * L * u

NetworkDiffusion (generic function with 1 method)

To run a simulation, we set some initial conditions and define an `ODEProblem` using `DifferentialEquations`

In [34]:
u0 = rand(N)
p = 2.0 
t_span = (0.0,1.0);


In [35]:
using DifferentialEquations

problem = ODEProblem(NetworkDiffusion, u0, (0.0,1.0), p);
sol = solve(problem, Tsit5(), saveat=0.05)

retcode: Success
Interpolation: 1st order linear
t: 21-element Array{Float64,1}:
 0.0
 0.05
 0.1
 0.15
 0.2
 0.25
 0.3
 0.35
 0.4
 0.45
 0.5
 0.55
 0.6
 0.65
 0.7
 0.75
 0.8
 0.85
 0.9
 0.95
 1.0
u: 21-element Array{Array{Float64,1},1}:
 [0.3490234218560442, 0.20805214718357723, 0.01270509990111024, 0.675004698909625, 0.7226958200397402]
 [0.3757392760552148, 0.2383757608314247, 0.08771852866814164, 0.5904333926508555, 0.6752142296844604]
 [0.3930462106944911, 0.2651826861672325, 0.1451980555310091, 0.5290850250110424, 0.6349692104863218]
 [0.40372967453235836, 0.28835750651726394, 0.1897903951297165, 0.4846747782134115, 0.6009288334973467]
 [0.4097993625733684, 0.30807224802428856, 0.2248195718513796, 0.45262622662529695, 0.5721637788157634]
 [0.4127006017968929, 0.324644624144038, 0.25267508087595736, 0.42960362072834835, 0.5478572603448604]
 [0.41346964874270725, 0.33844945993709086, 0.2750876982702358, 0.41317038233922554, 0.5273039986008374]
 [0.4128469842363713, 0.349868104687810

And we can view the solution. 

In [36]:
using Plots
plotly()
plot(sol)

<!DOCTYPE html>
 
 
 Plots.jl

### Inference

Now that we have a model, we generate some data and start to using `Turing` to perform inference.
To do this, we should define a generative model.

Our data $\mathbf{y}$ is given by a normal distribution centered around our model $f(\mathbf{u0}, \rho)$ with variance $\sigma$. 

$$\mathbf{y} = \mathcal{N}(f(\mathbf{u0}, \rho), \sigma)$$

and we assume our paramters are generated from the following distributions: 

$$\sigma \approx \Gamma^{-1}(2, 3)$$ 
$$\rho \approx \mathcal{N}(5,.10.[0,10])$$

We can make this into a `Turing` model. 





In [37]:
using Turing
Turing.setadbackend(:forwarddiff)
@model function fit(data::Array{Float64,2}, problem::ODEProblem, N::Int64)
    σ ~ InverseGamma(2, 3) # ~ is the tilde character
    ρ ~ truncated(Normal(5,10.0),0.0,10)
    u ~ filldist(truncated(Normal(0.5,2.0),0.0,1.0), N)

    prob = remake(problem, u0=u, p=ρ)
    predicted = solve(prob, Tsit5(),saveat=0.05)

    for i = 1:length(predicted)
        data[:,i] ~ MvNormal(predicted[i], σ)
    end
end

fit (generic function with 1 method)

To fit this model, we first need to generate some data. We can then feed in our data and our model into the `Turing` model and begin to sample from it. 

For now, we'll just use the data generated form our ODE solution above. 

In [38]:
data = Array(sol)

5×21 Array{Float64,2}:
 0.349023   0.375739   0.393046  0.40373   …  0.392186  0.391092  0.390155
 0.208052   0.238376   0.265183  0.288358     0.394998  0.395879  0.39657
 0.0127051  0.0877185  0.145198  0.18979      0.373943  0.376506  0.378726
 0.675005   0.590433   0.529085  0.484675     0.380406  0.380958  0.381535
 0.722696   0.675214   0.634969  0.600929     0.425947  0.423046  0.420496

#### MCMC Sampling 

We can now perform inference. First by initialising our `fit` function with synthetic data and our ODE problem. We can call initialise multiple chains to sampline in parallel -- here we use 10 chains. 

Once the sampling has completed, we can plot the chains to visualise convergence and posterior distributions of parameters.

In [39]:
model = fit(data, problem, N)
#chain = sample(model, NUTS(0.65), MCMCThreads(), 2000, 10, progres=false);
chain = sample(model, NUTS(0.65), 1000);

┌ Info: Found initial step size
│   ϵ = 0.2
└ @ Turing.Inference /home/chaggar/.julia/packages/Turing/XLLTf/src/inference/hmc.jl:188
Sampling: 100%|█████████████████████████████████████████| Time: 0:00:06


In [40]:
using StatsPlots
plot(chain)

<!DOCTYPE html>
 
 
 Plots.jl

In [41]:
chain

Chains MCMC chain (1000×19×1 Array{Float64,3}):

Iterations        = 1:1000
Thinning interval = 1
Chains            = 1
Samples per chain = 1000
parameters        = u[1], u[2], u[3], u[4], u[5], ρ, σ
internals         = acceptance_rate, hamiltonian_energy, hamiltonian_energy_error, is_accept, log_density, lp, max_hamiltonian_energy_error, n_steps, nom_step_size, numerical_error, step_size, tree_depth

Summary Statistics
  parameters      mean       std   naive_se      mcse        ess      rhat 
      Symbol   Float64   Float64    Float64   Float64    Float64   Float64 

        u[1]    0.3478    0.0124     0.0004    0.0004   938.9623    1.0002
        u[2]    0.2053    0.0179     0.0006    0.0009   453.1414    1.0050
        u[3]    0.0207    0.0143     0.0005    0.0007   546.9724    0.9991
        u[4]    0.6724    0.0166     0.0005    0.0010   643.3094    1.0019
        u[5]    0.7215    0.0151     0.0005    0.0007   440.5146    1.0015
           ρ    1.9950    0.1112     0.0035    0

### Summary
We can see from the plots and the chain summary that the chains converge and produce consistent estimates of the posterior distributions. Importantly, the posterior estimates closely correspond to the true model parameters.

With the ODE model and Turing model setup, we can begin to experiment with how inference is affected by changes to network topology and size.

## How Does Inference Scale with a Growing Network 

In this first experiment, we will test how well inference scales when we increase the size of the network used to simulate network diffusion. 

We can do this by initalising a new network with size `N` and plugging this into our ODEProblem and Turing model. 

### N = 10

In [42]:
N = 10
P = 0.5 

L, A = make_graph(N, P);



In [43]:
problem = ODEProblem(NetworkDiffusion, rand(N), (0.0,1.0), p);
data = Array(solve(problem, Tsit5(), saveat=0.05))

10×21 Array{Float64,2}:
 0.490989  0.516269  0.535046  0.54868   …  0.590087  0.590369  0.590597
 0.874023  0.803581  0.754403  0.718426     0.595648  0.594816  0.594151
 0.1423    0.363096  0.472799  0.52841      0.591524  0.591536  0.591544
 0.195663  0.325268  0.41145   0.468595     0.590402  0.590673  0.590879
 0.897814  0.764905  0.689219  0.645402     0.590006  0.590278  0.590506
 0.971048  0.851239  0.766841  0.70874   …  0.591297  0.591298  0.591314
 0.719983  0.639371  0.602592  0.587855     0.591865  0.591828  0.59179
 0.479774  0.481192  0.497023  0.515559     0.590409  0.590678  0.590882
 0.905694  0.828238  0.771514  0.728765     0.594242  0.593657  0.593202
 0.238233  0.342363  0.414633  0.465086     0.59004   0.590389  0.590656

In [44]:
plot(data')

<!DOCTYPE html>
 
 
 Plots.jl

In [45]:
model = fit(data, problem, N)
#chain = sample(model, NUTS(0.65), MCMCThreads(), 1000, 10, progres=false);
chain = sample(model, NUTS(0.65), 1000);

┌ Info: Found initial step size
│   ϵ = 0.2
└ @ Turing.Inference /home/chaggar/.julia/packages/Turing/XLLTf/src/inference/hmc.jl:188
Sampling:  12%|████▉                                    |  ETA: 0:00:27┌ Warning: The current proposal will be rejected due to numerical error(s).
│   isfinite.((θ, r, ℓπ, ℓκ)) = (true, false, false, false)
└ @ AdvancedHMC /home/chaggar/.julia/packages/AdvancedHMC/MIxdK/src/hamiltonian.jl:47
Sampling:  70%|████████████████████████████▋            |  ETA: 0:00:07┌ Warning: The current proposal will be rejected due to numerical error(s).
│   isfinite.((θ, r, ℓπ, ℓκ)) = (true, false, false, false)
└ @ AdvancedHMC /home/chaggar/.julia/packages/AdvancedHMC/MIxdK/src/hamiltonian.jl:47
Sampling: 100%|█████████████████████████████████████████| Time: 0:00:23


In [46]:
chain

Chains MCMC chain (1000×24×1 Array{Float64,3}):

Iterations        = 1:1000
Thinning interval = 1
Chains            = 1
Samples per chain = 1000
parameters        = u[1], u[2], u[3], u[4], u[5], u[6], u[7], u[8], u[9], u[10], ρ, σ
internals         = acceptance_rate, hamiltonian_energy, hamiltonian_energy_error, is_accept, log_density, lp, max_hamiltonian_energy_error, n_steps, nom_step_size, numerical_error, step_size, tree_depth

Summary Statistics
  parameters      mean       std   naive_se      mcse         ess      rhat 
      Symbol   Float64   Float64    Float64   Float64     Float64   Float64 

        u[1]    0.4906    0.0093     0.0003    0.0003   1028.5519    0.9992
        u[2]    0.8744    0.0099     0.0003    0.0003    925.6185    0.9992
        u[3]    0.1420    0.0130     0.0004    0.0005   1058.8014    1.0001
        u[4]    0.1953    0.0127     0.0004    0.0006    837.1765    0.9991
        u[5]    0.8978    0.0104     0.0003    0.0003   1071.2960    0.9991
        u[

In [47]:
plot(chain)

<!DOCTYPE html>
 
 
 Plots.jl

In [48]:
scatter(vcat(data[:,1],p,0))
scatter!(mean(chain).nt.mean)

<!DOCTYPE html>
 
 
 Plots.jl

#### Comment 
The results are stable, with tight distributions around the mean. The estimate for u3 is slightly off. This is plausibly due to the value beign close to the loewr bound of the truncated normal, such that steps further toward the true value have been rejected disproportionately to the relative importance of the region. 

### N = 25

In [49]:
N = 20
P = 0.5 

L, A = make_graph(N, P);

In [50]:
problem = ODEProblem(NetworkDiffusion, rand(N), (0.0,1.0), p);
data = Array(solve(problem, Tsit5(), saveat=0.05))
plot(data')

<!DOCTYPE html>
 
 
 Plots.jl

In [51]:
model = fit(data, problem, N)
chain = sample(model, NUTS(0.65), 1000)
#chain = sample(model, NUTS(0.65), MCMCThreads(), 1000, 10, progres=false);

┌ Info: Found initial step size
│   ϵ = 0.2
└ @ Turing.Inference /home/chaggar/.julia/packages/Turing/XLLTf/src/inference/hmc.jl:188
Sampling: 100%|█████████████████████████████████████████| Time: 0:01:50


In [52]:
plot(chain)

<!DOCTYPE html>
 
 
 Plots.jl

In [53]:
scatter(vcat(data[:,1],p,0))
scatter!(mean(chain).nt.mean)

<!DOCTYPE html>
 
 
 Plots.jl